# **\[SOLAR\]** GConvLSTM

JiyunLim  
2023-07-21

In [1]:
%run model_2023/ept_GConvLSTM.py

In [2]:
import itertools
import time

In [3]:
# read dataframe 
df = pd.read_csv('data_eng_230710.csv')

# make y, y_upper, y_period, time, regions 
y = df.loc[:,'Bukchoncheon':'Gyeongju-si'].to_numpy()
yU = df.loc[:,'Bukchoncheon_Upper':'Gyeongju-si_Upper'].to_numpy()
yP = np.divide(y, yU+1e-10)
t = df.loc[:,'date']
regions = list(df.loc[:,'Bukchoncheon':'Gyeongju-si'].columns)

TRAIN_RATIO = 0.8
T,N = len(t),len(regions) 
LEN_TEST = int(np.floor(T*(1-TRAIN_RATIO)))
LEN_TR = T - LEN_TEST

In [4]:
import datetime
from tqdm import tqdm

In [ ]:
method = ['classic','proposed']
lags = [4]   # [4, 8, 12, 24]
filters = [4, 8, 16, 32] 
epoch = [10, 30] 

# model_name = 'RecurrentGCN' ### 모델변경시 수정필요
model_name = 'GConvLSTM'

col = ['model', 'method', 'lags', 
       'nof_filters', 'epoch', 'calculation_time',
       'index_time',
       'node', 'mse']
df = pd.DataFrame(columns=col)


for iteration in tqdm(range(50)): ###
    for m,l,f,e in itertools.product(method, lags, filters, epoch):
        if m == 'classic':
            t1 = time.time()
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yhat = rgcn(y, model = model, train_ratio = TRAIN_RATIO, lags=l, epoch=e)
            yhat[yhat < 0]= 0   
            t2 = time.time()
            c = t2-t1
            t = str(datetime.datetime.now())
            _df2 = pd.concat([pd.Series(regions),pd.Series(((y - yhat)[LEN_TR:, :] ** 2).mean(axis=0))],axis=1)
            _df1 = pd.DataFrame([[model_name,m,l,f,e,c,t]]*N)
            _df = pd.concat([_df1,_df2],axis=1).set_axis(col,axis=1)
            df = pd.concat([df,_df])
        else: # proposed 
            t1 = time.time()
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yUhat = rgcn(yU, model = model, train_ratio = 0.8, lags=l, epoch=e)
            model = RecurrentGCN(node_features=l, filters=f) ### 모델변경시 수정필요
            yPhat = rgcn(yP, model = model, train_ratio = 0.8, lags=l, epoch=e)
            yPhat[yPhat < 0] =0 
            yhat = yUhat*yPhat
            t2 = time.time()
            c = t2-t1
            t = str(datetime.datetime.now())
            _df2 = pd.concat([pd.Series(regions),pd.Series(((y - yhat)[LEN_TR:, :] ** 2).mean(axis=0))],axis=1)
            _df1 = pd.DataFrame([[model_name,m,l,f,e,c,t]]*N)
            _df = pd.concat([_df1,_df2],axis=1).set_axis(col,axis=1)
            df = pd.concat([df,_df])

  0%|          | 0/50 [00:00<?, ?it/s]  2%|▏         | 1/50 [1:40:02<81:42:13, 6002.72s/it]  4%|▍         | 2/50 [3:24:06<81:55:29, 6144.37s/it]  6%|▌         | 3/50 [5:15:50<83:33:18, 6399.97s/it]  8%|▊         | 4/50 [6:58:56<80:41:54, 6315.54s/it]

30/3030/3030/3030/3030/30

In [13]:
df.head()

In [12]:
path = './RLST/GConvLSTM/'
df.to_csv(path+'GConvLSTM_LAG4.csv', index=False)

In [10]:
df_summary = df.groupby(by=['method', 'nof_filters', 'epoch']).agg({'mse':[np.mean, np.std]}).reset_index()
df_summary[df_summary['epoch']==10]

In [11]:
df_summary[df_summary['epoch']==30]

-   GConvLSTM의 경우 classic방법이 훨씬 좋다..